##Ingest gamelist.json file

In [0]:
%run "../2.utils/0.configuration"

#### 1 - Read the json file using the spark dataframe reader

###### 1.1 import functions

In [0]:
from pyspark.sql.functions import current_timestamp, lit, to_date, regexp_replace, to_timestamp, current_date
from delta.tables import DeltaTable

###### 1.2 read games.csv with defined schema

In [0]:
games_df = spark.read.json(f"{raw_path}/gamelist.json", multiLine=True)

###### 1.3 check dataframe output

In [0]:
display(games_df)

about_the_game achievements appid categories currency detailed_description developers dlc_count genres header_image linux mac metacritic_score metacritic_url name notes price publishers recommendations release_date required_age reviews short_description windows After over a decade of top-secret research, an international cabal of neuroscientists, systems engineers, and Chaucer scholars is pleased to announce the re-release of I MAED A GAM3 W1TH Z0MB1ES 1N IT!!!1 .This release represents the culmination of 12 years of focused interdisciplinary investigation and improv cults, and its groundbreaking achievements in design, philosophy, and metaphysics are poised to disrupt, enthrall, and terrify. This top down twin-stick shooter will bring you tremendous amounts of fun. The best selling Xbox Live Indie Game of 2009, I Made A Game With Zombies In It!!! has been revamped with a whole new engine! The game now supports keyboard and mouse, has a flashing lights reduction mode, and will soon even have ONLINE MULTIPLAYER!! Despite being free, we will be adding a few new features and bugfixes over time to improve the game even further. Despite only taking 10 minutes of your time, we know this is a game we just know you will play again and again! Theres a reason why Youtube videos of this game have comments sections filled to the brim with requests for a Steam port. So what are you waiting for?! LETS KILL SOME ZOMBIES!!!1! 1 1800730 List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Full controller support, Remote Play Together) EUR After over a decade of top-secret research, an international cabal of neuroscientists, systems engineers, and Chaucer scholars is pleased to announce the re-release of I MAED A GAM3 W1TH Z0MB1ES 1N IT!!!1 .This release represents the culmination of 12 years of focused interdisciplinary investigation and improv cults, and its groundbreaking achievements in design, philosophy, and metaphysics are poised to disrupt, enthrall, and terrify. This top down twin-stick shooter will bring you tremendous amounts of fun. The best selling Xbox Live Indie Game of 2009, I Made A Game With Zombies In It!!! has been revamped with a whole new engine! The game now supports keyboard and mouse, has a flashing lights reduction mode, and will soon even have ONLINE MULTIPLAYER!! Despite being free, we will be adding a few new features and bugfixes over time to improve the game even further. Despite only taking 10 minutes of your time, we know this is a game we just know you will play again and again! Theres a reason why Youtube videos of this game have comments sections filled to the brim with requests for a Steam port. So what are you waiting for?! LETS KILL SOME ZOMBIES!!!1! List(Ska Studios, OMNIViOLET) 0 List(Action, Casual, Free to Play, Indie) https://cdn.akamai.steamstatic.com/steam/apps/1800730/header.jpg?t=1636653238 true false 0 I MAED A GAM3 W1TH Z0MB1ES 1N IT!!!1 Warning, this game features blood and gore in the form of zombie slaying. 0.0 List(Ska Studios) 0 11 Nov, 2021 0 A top down twin stick zombie slaying shooter that you are sure to play again and again! true Find Her in Dungeon - 3D Quest with a variety of actions, where U have to solve (as in quests) your further passage. The main character gets into a dungeon, where the main goal is to find the girl. The game contains a variety of tasks for further advancement, since this is a quest, good intuition is required. There will be moments of joy and fear during the game. Be prepared. In many ways, the game was created precisely for the purpose that you enjoy the game. The game also has magic, but to master it you will need to find the necessary artifacts. Fully immerse yourself in the game and enjoy it. 0 1800780 List(Single-player) EUR Find Her in Dungeon - 3D Quest with a variety of actions, where U have to solve (as in quests) your further passage. The main character gets into a dungeon, where the main goal is to find the girl. T

#### 2 - Select wanted columns / fix release date and add create/update timestamps

In [0]:
selected_games_df = games_df.select(
                                    games_df["appid"],
                                    games_df["name"],
                                    games_df["release_date"],
                                    games_df["price"],
                                    games_df["currency"],
                                    games_df["short_description"],
                                    games_df["header_image"],
                                    games_df["windows"],
                                    games_df["mac"],
                                    games_df["linux"],
                                    games_df["metacritic_score"],
                                    games_df["developers"],
                                    games_df["publishers"],
                                    games_df["categories"],
                                    games_df["genres"])\
                                    .withColumn("release_date", regexp_replace("release_date", ",", ''))\
                                    .withColumn("release_date", to_date("release_date", format='d MMM yyyy'))\
                                    .withColumn("create_timestamp",current_timestamp())\
                                    .withColumn("update_timestamp",lit(""))

###### 2.1 check dataframe output for selected columns

In [0]:
display(selected_games_df)

appid name release_date price currency short_description header_image windows mac linux metacritic_score developers publishers categories genres create_timestamp update_timestamp 1800730 I MAED A GAM3 W1TH Z0MB1ES 1N IT!!!1 2021-11-11 0.0 EUR A top down twin stick zombie slaying shooter that you are sure to play again and again! https://cdn.akamai.steamstatic.com/steam/apps/1800730/header.jpg?t=1636653238 true false true 0 List(Ska Studios, OMNIViOLET) List(Ska Studios) List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Full controller support, Remote Play Together) List(Action, Casual, Free to Play, Indie) 2022-09-11T14:49:15.521+0000 1800780 Find Her in Dungeon (3D Quest) 2021-11-30 0.79 EUR Find Her in Dungeon - 3D Quest with a variety of actions, where U have to solve (as in quests) your further passage. Sometimes it's fun, sometimes it's scary, sometimes it's sad. With the help of hints and logic, try to find her. https://cdn.akamai.steamstatic.com/steam/apps/1800780/header.jpg?t=1638339294 true false false 0 List(Hedgehog) List(Hedgehog Games) List(Single-player) List(Adventure, Indie) 2022-09-11T14:49:15.521+0000 1800830 Russian Drunken Boxers 2 2021-11-12 8.99 EUR New fights of drunken Russian boxers at night. Spoof your friend or Ai bot using empty bottles of alcohol. Use super abilities https://cdn.akamai.steamstatic.com/steam/apps/1800830/header.jpg?t=1654492377 true false false 0 List(Svarovsky) List(Gales Corp.) List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Steam Achievements, Remote Play Together) List(Action, Indie, Sports) 2022-09-11T14:49:15.521+0000 1800900 SpaceGaze 2021-11-15 11.59 EUR SpaceGaze is a space arena shooter in which you have to destroy hordes of space invaders from another universe. https://cdn.akamai.steamstatic.com/steam/apps/1800900/header.jpg?t=1650352712 true false false 0 List(galesoozka) List(galesoozka) List(Single-player, Steam Achievements) List(Indie, Simulation, Sports) 2022-09-11T14:49:15.521+0000 1800920 Medusa's Heart of Stone Chapter 01 2022-03-15 0.0 EUR Medusa's Heart of Stone is a 2D narrative driven game with action sequences, puzzles and quest interspersed throughout. Feared by mortals and forsaken by the gods, Medusa embarks on a journey to find someone who could love her. https://cdn.akamai.steamstatic.com/steam/apps/1800920/header.jpg?t=1647374260 true false false 0 List(Tired Moon Studios) List(Milpitians) List(Single-player) List(Adventure, Indie) 2022-09-11T14:49:15.521+0000 1800970 Arcade Galaxy 2021-11-12 8.19 EUR Arcade Galaxy - a game made in 2D-hand-drawn graphics, which is a space arcade in a retro style. https://cdn.akamai.steamstatic.com/steam/apps/1800970/header.jpg?t=1636744205 true false false 0 List(Crooked Road) List(Piece Of Voxel) List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Remote Play Together) List(Action, Adventure, Indie, Simulation) 2022-09-11T14:49:15.521+0000 1800980 Fish Story 2021-11-11 0.79 EUR Atmospheric underwater game for the whole family! Help the brave fish solve the mystery of the lights! https://cdn.akamai.steamstatic.com/steam/apps/1800980/header.jpg?t=1643887804 true false true 0 List(Five Percents) List(Five Percents) List(Single-player, Steam Achievements, Steam Cloud) List(Action, Adventure, Casual, Indie) 2022-09-11T14:49:15.521+0000 1801000 Traffic Racing 2021-11-12 8.99 EUR Traffic Racing is a 3D car simulator, you play as the racer Ron, on the highway, overtake as many cars as possible, and do not get off the highway https://cdn.akamai.steamstatic.com/steam/apps/1801000/header.jpg?t=1654492888 true false false 0 List(REALBB) List(Gales Corp.) List(Single-player) List(Casual, Indie, Simulation) 2022-09-11T14:49:15.521+0000 1801060 Helix 2021-11-22 0.0 EUR Helix is a low-poly multiplayer FPS Hero-Shooter with MOBA-like Mechanics where during a match you will have to kill your opponents and steal their DNA

#### 3 - Clean Data

In [0]:
final_df = selected_games_df.na.drop(subset=["release_date"])

###### 3.1 check final dataframe output

In [0]:
display(final_df)

appid name release_date price currency short_description header_image windows mac linux metacritic_score developers publishers categories genres create_timestamp update_timestamp 1800730 I MAED A GAM3 W1TH Z0MB1ES 1N IT!!!1 2021-11-11 0.0 EUR A top down twin stick zombie slaying shooter that you are sure to play again and again! https://cdn.akamai.steamstatic.com/steam/apps/1800730/header.jpg?t=1636653238 true false true 0 List(Ska Studios, OMNIViOLET) List(Ska Studios) List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Full controller support, Remote Play Together) List(Action, Casual, Free to Play, Indie) 2022-09-11T14:49:16.316+0000 1800780 Find Her in Dungeon (3D Quest) 2021-11-30 0.79 EUR Find Her in Dungeon - 3D Quest with a variety of actions, where U have to solve (as in quests) your further passage. Sometimes it's fun, sometimes it's scary, sometimes it's sad. With the help of hints and logic, try to find her. https://cdn.akamai.steamstatic.com/steam/apps/1800780/header.jpg?t=1638339294 true false false 0 List(Hedgehog) List(Hedgehog Games) List(Single-player) List(Adventure, Indie) 2022-09-11T14:49:16.316+0000 1800830 Russian Drunken Boxers 2 2021-11-12 8.99 EUR New fights of drunken Russian boxers at night. Spoof your friend or Ai bot using empty bottles of alcohol. Use super abilities https://cdn.akamai.steamstatic.com/steam/apps/1800830/header.jpg?t=1654492377 true false false 0 List(Svarovsky) List(Gales Corp.) List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Steam Achievements, Remote Play Together) List(Action, Indie, Sports) 2022-09-11T14:49:16.316+0000 1800900 SpaceGaze 2021-11-15 11.59 EUR SpaceGaze is a space arena shooter in which you have to destroy hordes of space invaders from another universe. https://cdn.akamai.steamstatic.com/steam/apps/1800900/header.jpg?t=1650352712 true false false 0 List(galesoozka) List(galesoozka) List(Single-player, Steam Achievements) List(Indie, Simulation, Sports) 2022-09-11T14:49:16.316+0000 1800920 Medusa's Heart of Stone Chapter 01 2022-03-15 0.0 EUR Medusa's Heart of Stone is a 2D narrative driven game with action sequences, puzzles and quest interspersed throughout. Feared by mortals and forsaken by the gods, Medusa embarks on a journey to find someone who could love her. https://cdn.akamai.steamstatic.com/steam/apps/1800920/header.jpg?t=1647374260 true false false 0 List(Tired Moon Studios) List(Milpitians) List(Single-player) List(Adventure, Indie) 2022-09-11T14:49:16.316+0000 1800970 Arcade Galaxy 2021-11-12 8.19 EUR Arcade Galaxy - a game made in 2D-hand-drawn graphics, which is a space arcade in a retro style. https://cdn.akamai.steamstatic.com/steam/apps/1800970/header.jpg?t=1636744205 true false false 0 List(Crooked Road) List(Piece Of Voxel) List(Single-player, Multi-player, Co-op, Shared/Split Screen Co-op, Shared/Split Screen, Remote Play Together) List(Action, Adventure, Indie, Simulation) 2022-09-11T14:49:16.316+0000 1800980 Fish Story 2021-11-11 0.79 EUR Atmospheric underwater game for the whole family! Help the brave fish solve the mystery of the lights! https://cdn.akamai.steamstatic.com/steam/apps/1800980/header.jpg?t=1643887804 true false true 0 List(Five Percents) List(Five Percents) List(Single-player, Steam Achievements, Steam Cloud) List(Action, Adventure, Casual, Indie) 2022-09-11T14:49:16.316+0000 1801000 Traffic Racing 2021-11-12 8.99 EUR Traffic Racing is a 3D car simulator, you play as the racer Ron, on the highway, overtake as many cars as possible, and do not get off the highway https://cdn.akamai.steamstatic.com/steam/apps/1801000/header.jpg?t=1654492888 true false false 0 List(REALBB) List(Gales Corp.) List(Single-player) List(Casual, Indie, Simulation) 2022-09-11T14:49:16.316+0000 1801060 Helix 2021-11-22 0.0 EUR Helix is a low-poly multiplayer FPS Hero-Shooter with MOBA-like Mechanics where during a match you will have to kill your opponents and steal their DNA

#### 4 - Write dataframe to delta table.
* Check if table exists
* If table exists check for old and new results
* Update timestamp if appid already exists
* Insert everything new if row dont exist

In [0]:
if (spark._jsparkSession.catalog().tableExists("steam_processed.games")):
    deltaTable = DeltaTable.forPath(spark, f"{processed_path}/games")
    deltaTable.alias("tgt").merge(
        final_df.alias("src"),
        "tgt.appid = src.appid") \
      .whenMatchedUpdate(set={"update_timestamp": current_timestamp()}) \
      .whenNotMatchedInsertAll()\
      .execute()
else:
    final_df.write.mode("overwrite").format("delta").saveAsTable("steam_processed.games")

###### 4.1 Test read of delta table

In [0]:
%sql SELECT * FROM steam_processed.games where release_date >= '2022-01-01' ORDER BY release_date DESC;

appid name release_date price currency short_description header_image windows mac linux metacritic_score developers publishers categories genres create_timestamp update_timestamp 1798610 International Medical Station 2022-09-05 12.49 EUR ~1300 drugs - ~33000 information (paragraphs and info pieces) - ~7000 information actually used Updates will be constantly made. Stay tuned. https://cdn.akamai.steamstatic.com/steam/apps/1798610/header.jpg?t=1662440232 true false false 0 List(Planet Muses) List(Planet Muses) List() List(Education, Utilities) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 1664580 Terra Ventura 2022-09-05 9.99 EUR Terra Ventura is a classic style action RPG combined with modern, streamlined sub-systems; random loot, skill tree paths, player development and character customization. Push your way through the handcrafted maps using real time combat or acquired skills. https://cdn.akamai.steamstatic.com/steam/apps/1664580/header.jpg?t=1662379615 true false true 0 List(Logical Progression Games) List(Logical Progression Games) List(Single-player, Steam Achievements, Steam Leaderboards) List(Action, Indie, RPG) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 1827290 Turpedo 2022-09-04 3.99 EUR A fast paced 2-4 multiplayer party game where players incarnate submarines for victory over polluted oceans. Evolve as you play with a range of mutations in round based combat over multiple game modes. https://cdn.akamai.steamstatic.com/steam/apps/1827290/header.jpg?t=1662332223 true false false 0 List(Myles Lambert) List(Myles Lambert) List(Multi-player, PvP, Online PvP, Shared/Split Screen PvP, Shared/Split Screen, Full controller support, Remote Play Together) List(Action, Casual, Indie) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 1707570 Merchant's Game 2022-09-01 2.39 EUR Merchant's Game is a 2D pixelart open-ended game that you hire npc's, negotiate prices, sell and buy items to pay your debt to the lanlord and maintaining your shop. https://cdn.akamai.steamstatic.com/steam/apps/1707570/header.jpg?t=1662060138 true false false 0 List(CAN UNIVERSE) List(CAN UNIVERSE) List(Single-player) List(Adventure, Indie, Simulation) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 2126760 Lurch Playtest 2022-09-01 0.0 EUR https://cdn.akamai.steamstatic.com/steam/apps/2126760/header.jpg?t=1662088799 true false false 0 List() List() List() List() 2022-09-11T14:46:31.040+0000 2022-09-11 14:49:17.05 1758930 Dream of Light 2022-09-01 0.0 EUR This is a walking simulator developed by Unreal 4. The scene contains a certain amount of fragmented dialogue content. It tells the story of a young girl who left her hometown to venture into the outside world. ....... https://cdn.akamai.steamstatic.com/steam/apps/1758930/header.jpg?t=1662017606 true false false 0 List(The Dream) List(The Dream) List(Single-player) List(Adventure, Casual, Indie) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 1723750 BarginToWin 2022-09-01 1.59 EUR BarginToWin is trade bargain simulation game that you buy cheap and sell for profit! https://cdn.akamai.steamstatic.com/steam/apps/1723750/header.jpg?t=1662087247 true false false 0 List(mike9973) List(SpaceFlyTeam) List(Single-player) List(Casual, Indie, Simulation, Strategy, Early Access) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 1763180 Wormatozoa 2022-08-31 5.69 EUR A gross 2D point-and-click precision platformer about parasitic worms. Guide them through a human body as they evolve from tiny parasites to city-engulfing monsters in this tough-as-nails arcade slither-em-up! https://cdn.akamai.steamstatic.com/steam/apps/1763180/header.jpg?t=1661973156 true true false 0 List(distributive) List(distributive) List(Single-player, Steam Achievements) List(Action, Indie) 2022-09-11T13:15:34.164+0000 2022-09-11 14:49:17.05 1710790 Finley's - The Colour of Radiation 2022-08-31 5.69 EUR A puzzle solving game of laser light beams, refraction, reflection and mixing. Pit your wits against the maniacal a

In [0]:
dbutils.notebook.exit("ended successfully")

ended successfully

###### 4.2 small data tests and data verifying

In [0]:
%sql select count(appid) from steam_processed.games;

In [0]:
%sql select count(appid) from steam_processed.games;

In [0]:
%sql select appid, count(1) as counter from steam_processed.games group by appid having counter > 1;